In [0]:
%python
# Set up and connect to Azure Data Lake Store Gen2

storage_name = dbutils.widgets.get("storage_account_name")
storage_access_key = dbutils.widgets.get("access_key")
staging_container = dbutils.widgets.get("staging_container")
curated_container = dbutils.widgets.get("curated_container")
curated_data_path = dbutils.widgets.get("curated_data_path")
staging_data_path = dbutils.widgets.get("staging_data_path")


spark.conf.set(f"fs.azure.account.key.{storage_name}.dfs.core.windows.net", f"{storage_access_key}")

file_path = f"abfss://{staging_container}@datalake876.dfs.core.windows.net/{staging_data_path}"

# Read the data from Azure Data Lake Store Gen2 and convert to pandas dataframe from Spark
df = spark.read.format("csv").option("header", "true").load(file_path)

In [0]:
#drop missing values and duplicate rows
df = df.dropna()
df = df.dropDuplicates()

In [0]:
# Update data types for the columns
df = df.withColumn("SeniorCitizen", df["SeniorCitizen"].cast("int").cast("boolean"))

In [0]:
#updating the yes/no only columns to boolean values of true/false
from pyspark.sql.functions import col, lower, when

replacement_values = {'yes': True, 'no': False}
string_cols_to_bool = ['Partner', 'Dependents', 'PhoneService', 'PaperlessBilling', 'Churn']

for col_name in string_cols_to_bool:
    df = df.withColumn(col_name, when(lower(col(col_name)) == 'yes', True).otherwise(False))

In [0]:
#updating the data types of the numeric columns
df = df.withColumn("TotalCharges", col("TotalCharges").cast("float"))
df = df.withColumn("MonthlyCharges", col("MonthlyCharges").cast("float"))
df = df.withColumn("tenure", col("tenure").cast("int"))

In [0]:
#create the valuesegment column based on monthly charges and total charges
df = df.withColumn(
    'ValueSegment',
    when((col('TotalCharges') >= 7000) | (col('MonthlyCharges') >= 90), 'High Value')
    .when((col('TotalCharges') >= 3000) | (col('MonthlyCharges') >= 40), 'Medium Value')
    .otherwise('Low Value')
)

In [0]:

df = df.withColumn(
    'TenureBucket',
    when(col('tenure') <= 11, '0-11 Months')
    .when((col('tenure') <= 23), '12-23 Months')
    .when((col('tenure') <= 35), '24-35 Months')
    .when((col('tenure') <= 47), '36-47 Months')
    .when((col('tenure') <= 59), '48-59 Months')
    .otherwise('60+ Months')
)

# Display the updated DataFrame
display(df)

customerID gender SeniorCitizen Partner Dependents tenure PhoneService MultipleLines InternetService OnlineSecurity OnlineBackup DeviceProtection TechSupport StreamingTV StreamingMovies Contract PaperlessBilling PaymentMethod MonthlyCharges TotalCharges Churn ValueSegment TenureBucket 7590-VHVEG Female false true false 1 false No phone service DSL No Yes No No No No Month-to-month true Electronic check 29.85 29.85 false Low Value 0-11 Months 5575-GNVDE Male false false false 34 true No DSL Yes No Yes No No No One year false Mailed check 56.95 1889.5 false Medium Value 24-35 Months 3668-QPYBK Male false false false 2 true No DSL Yes Yes No No No No Month-to-month true Mailed check 53.85 108.15 true Medium Value 0-11 Months 7795-CFOCW Male false false false 45 false No phone service DSL Yes No Yes Yes No No One year false Bank transfer (automatic) 42.3 1840.75 false Medium Value 36-47 Months 9237-HQITU Female false false false 2 true No Fiber optic No No No No No No Month-to-month true Electronic check 70.7 151.65 true Medium Value 0-11 Months 9305-CDSKC Female false false false 8 true Yes Fiber optic No No Yes No Yes Yes Month-to-month true Electronic check 99.65 820.5 true High Value 0-11 Months 1452-KIOVK Male false false true 22 true Yes Fiber optic No Yes No No Yes No Month-to-month true Credit card (automatic) 89.1 1949.4 false Medium Value 12-23 Months 6713-OKOMC Female false false false 10 false No phone service DSL Yes No No No No No Month-to-month false Mailed check 29.75 301.9 false Low Value 0-11 Months 7892-POOKP Female false true false 28 true Yes Fiber optic No No Yes Yes Yes Yes Month-to-month true Electronic check 104.8 3046.05 true High Value 24-35 Months 6388-TABGU Male false false true 62 true No DSL Yes Yes No No No No One year false Bank transfer (automatic) 56.15 3487.95 false Medium Value 60+ Months 9763-GRSKD Male false true true 13 true No DSL Yes No No No No No Month-to-month true Mailed check 49.95 587.45 false Medium Value 12-23 Months 7469-LKBCI Male false false false 16 true No No No internet service No internet service No internet service No internet service No internet service No internet service Two year false Credit card (automatic) 18.95 326.8 false Low Value 12-23 Months 8091-TTVAX Male false true false 58 true Yes Fiber optic No No Yes No Yes Yes One year false Credit card (automatic) 100.35 5681.1 false High Value 48-59 Months 0280-XJGEX Male false false false 49 true Yes Fiber optic No Yes Yes No Yes Yes Month-to-month true Bank transfer (automatic) 103.7 5036.3 true High Value 48-59 Months 5129-JLPIS Male false false false 25 true No Fiber optic Yes No Yes Yes Yes Yes Month-to-month true Electronic check 105.5 2686.05 false High Value 24-35 Months 3655-SNQYZ Female false true true 69 true Yes Fiber optic Yes Yes Yes Yes Yes Yes Two year false Credit card (automatic) 113.25 7895.15 false High Value 60+ Months 8191-XWSZG Female false false false 52 true No No No internet service No internet service No internet service No internet service No internet service No internet service One year false Mailed check 20.65 1022.95 false Low Value 48-59 Months 9959-WOFKT Male false false true 71 true Yes Fiber optic Yes No Yes No Yes Yes Two year false Bank transfer (automatic) 106.7 7382.25 false High Value 60+ Months 4190-MFLUW Female false true true 10 true No DSL No No Yes Yes No No Month-to-month false Credit card (automatic) 55.2 528.35 true Medium Value 0-11 Months 4183-MYFRB Female false false false 21 true No Fiber optic No Yes Yes No No Yes Month-to-month true Electronic check 90.05 1862.9 false High Value 12-23 Months 8779-QRDMV Male true false false 1 false No phone service DSL No No Yes No No Yes Month-to-month true Electronic check 39.65 39.65 true Low Value 0-11 Months 1680-VDCWW Male false true false 12 true No No No internet service No internet service No internet service No internet service No internet service No internet service One year false Bank transfer (automatic) 19.8 202.25 fals

In [0]:
#write the file to a CSV in the curated container

df.write.format("csv").option("header", "true").mode("overwrite").save(f"abfss://{curated_container}@datalake876.dfs.core.windows.net/{curated_data_path}")